In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
# Import all the necessary modules
import keysight.qcs as qcs

from keysight.qcs.channels import ChannelMapper
from keysight.qcs.executor import Executor, HclBackend
from keysight.qcs.experiments import make_calibration_set

from keysight.qcs.interfaces import QASMConverter as translate

In [3]:
# Path to QASM file
qasm_path = "<path/to/qasm/file.qasm>"

# QASM code in string format
qasm_str = """
OPENQASM 2.0;
include "qelib1.inc";

qreg q[1];  // A quantum register with 5 qubits
creg c[1];  // A classical register with 5 bits for measurement

// Apply single qubit rotation gates
rx(pi) q[0];
ry(pi) q[0];

// Measure the output
measure q[0] -> c[0];
"""

In [4]:
# Set this to True if you want to use a QASM file from a path
use_program_from_path = False

if use_program_from_path:
    qasm_program = translate(qasm_path)
else:
    qasm_program = translate(qasm_str)

# Visualizes the QCS program
qasm_program.qcs_program

Program([Layer([ParameterizedGate(gate=ParametricGate(layers=[[Hamiltonian(matrix=[[(-1.1102230246251565e-16+0j), (0.9999999999999994+0j)], [(0.9999999999999994+0j), (-5.551115123125783e-17+0j)]]), name=SIGMA_X)]], parameters=[[phi_x]], name=RX), parameters=(Scalar(name=_implicit, value=3.141592653589793, dtype=float, unit=none),), name=RX), ParameterizedGate(gate=ParametricGate(layers=[[Hamiltonian(matrix=[[(-1.1102230246251565e-16+0j), 0.9999999999999994j], [-0.9999999999999994j, (-5.551115123125783e-17+0j)]]), name=SIGMA_Y)]], parameters=[[phi_y]], name=RY), parameters=(Scalar(name=_implicit, value=3.141592653589793, dtype=float, unit=none),), name=RY), Measure(2)])])

In [5]:
# View the transpiled QCS program
qasm_program.transpiled_program

Program([Layer([ParameterizedGate(gate=ParametricGate(layers=[[Hamiltonian(matrix=[[(1+0j), 0j], [0j, (-1+0j)]]), name=SIGMA_Z)]], parameters=[[phi_z]], name=RZ), parameters=(Scalar(name=_implicit, value=0.0, dtype=float, unit=none),), name=RZ), ParameterizedGate(gate=ParametricGate(layers=[[Hamiltonian(matrix=[[(-1.1102230246251565e-16+0j), (0.9999999999999994+0j)], [(0.9999999999999994+0j), (-5.551115123125783e-17+0j)]]), name=SIGMA_X)]], parameters=[[phi_x]], name=RX), parameters=(Scalar(name=_implicit, value=3.141592653589793, dtype=float, unit=none),), name=RX), ParameterizedGate(gate=ParametricGate(layers=[[Hamiltonian(matrix=[[(1+0j), 0j], [0j, (-1+0j)]]), name=SIGMA_Z)]], parameters=[[phi_z]], name=RZ), parameters=(Scalar(name=_implicit, value=0.0, dtype=float, unit=none),), name=RZ), ParameterizedGate(gate=ParametricGate(layers=[[Hamiltonian(matrix=[[(1+0j), 0j], [0j, (-1+0j)]]), name=SIGMA_Z)]], parameters=[[phi_z]], name=RZ), parameters=(Scalar(name=_implicit, value=3.141592

In [6]:
# Set this to True if calibration set already exists
calibration_set_exists = False
if calibration_set_exists:
    calibration_set = qcs.load("<path/to/calibration_set.qcs>")
else:
    # Make a template calibration set
    calibration_set = make_calibration_set(qcs.Qudits(range(5), name="q"))

# Compile the program for execution on QCS hardware
compiled_program = qasm_program.compile_program(calibration_set)
compiled_program.draw()

In [7]:
# Render the compiled program
compiled_program.render(sample_rate=5e9, channel_subplots=False)

In [8]:
# Set this to True if channel mapper exists
channel_mapper_exists = False

if channel_mapper_exists:
    mapper = qcs.load("<path/to/channel_mapper.qcs>")
else:
    # generate an empty channel mapper with the correct ip address (for remote jobs)
    mapper = ChannelMapper("<ip_address>")

In [9]:
# Set this to True if you want to run on hardware
run_on_hw = False
fpga_postprocessing = (
    False  # Refers to hardware demodulation, if True returns only I/Q data
)

if run_on_hw:
    backend = HclBackend(channel_mapper=mapper, fpga_postprocessing=fpga_postprocessing)
    qasm_executed = Executor(backend).execute(compiled_program)
else:
    # load in a previously executed version of this experiment
    qasm_executed = qcs.load("QASM_program.hdf5")

In [10]:
qasm_executed.plot_trace()

In [11]:
qasm_1 = """
OPENQASM 2.0;
include "qelib1.inc";

qreg q[1];  // A quantum register with 5 qubits
creg c[1];  // A classical register with 5 bits for measurement

// Apply single qubit rotation gates
rx(pi) q[0];
ry(pi) q[0];

// Measure the output
measure q[0] -> c[0];
"""

In [12]:
qasm_2 = """
OPENQASM 2.0;
include "qelib1.inc";

qreg q[1];  // A quantum register with 5 qubits
creg c[1];  // A classical register with 5 bits for measurement

// Apply single qubit rotation gates
rx(pi/2) q[0];
ry(pi/2) q[0];

// Measure the output
measure q[0] -> c[0];
"""

In [13]:
qasm_3 = """
OPENQASM 2.0;
include "qelib1.inc";

qreg q[1];  // A quantum register with 5 qubits
creg c[1];  // A classical register with 5 bits for measurement

// Apply single qubit rotation gates
rx(pi/4) q[0];
ry(pi/4) q[0];

// Measure the output
measure q[0] -> c[0];
"""

In [14]:
# Path to QASM programs
qasm_dir = "<path/to/list/of/qasm/programs>"

# List of QASM circuits defined above
qasm_circuits = [qasm_1, qasm_2, qasm_3]

# Set this to True if you want to use QASM files from a directory path
use_program_from_path = False

qasm_path = qasm_dir if use_program_from_path else qasm_circuits

compiled_program = translate.from_group(qasm_path, calibration_set)
compiled_program[0].draw()

In [15]:
compiled_program, gate_programs, transpiled_programs = translate.from_group(
    batch=qasm_path, calibration_set=calibration_set, gate_level=True
)

for program in gate_programs:
    program.draw()

In [16]:
# Render the compiled program
compiled_program[0].render(sample_rate=5e9, channel_subplots=False, sweep_index=1)

In [17]:
# Set this to True if channel mapper exists
channel_mapper_exists = False

if channel_mapper_exists:
    mapper = qcs.load("<path/to/channel_mapper.qcs>")
else:
    # generate an empty channel mapper with the correct ip address (for remote jobs)
    mapper = ChannelMapper("<ip_address>")

In [18]:
# Set this to True if you want to run on hardware
run_on_hw = False
fpga_postprocessing = (
    False  # Refers to hardware demodulation, if True returns only I/Q data
)

if run_on_hw:
    backend = HclBackend(channel_mapper=mapper, fpga_postprocessing=fpga_postprocessing)
    qasm_executed = Executor(backend).execute(compiled_program)
else:
    # load in a previously executed version of this experiment
    qasm_executed = qcs.load("QASM_program_from_group.hdf5")

In [19]:
# Turn this to true to see the legend
legend = False

fig = qasm_executed.plot_trace()
fig.update_layout(showlegend=legend)
fig.show()